# Math 124 - Programming for Mathematical Applications
Per-Olof Persson, UC Berkeley

## Homework 11

### Preliminaries: Graph Structures and Functions

Before tackling the problems, we need to set up our toolkit. The cell below contains the `Graph` and `Vertex` data structures, along with the `shortest_path_bfs` and plotting functions adapted from the lecture notes. We'll use these as building blocks for this homework.

In [ ]:
using Plots, SparseArrays   # Packages needed

struct Vertex
    # A list of integers (indices) specifying which vertices this vertex points to
    neighbors::Vector{Int}       
    
    # 2D coordinates [x, y] for plotting (optional)
    coordinates::Vector{Float64} 
    
    # An inner constructor to provide a default value for coordinates
    Vertex(neighbors; coordinates=[0,0]) = new(neighbors, coordinates)
end

# This overloads the 'show' function to print a Vertex more nicely
function Base.show(io::IO, v::Vertex)
    print(io, "Neighbors = ", v.neighbors)
end

struct Graph
    # A list containing all the Vertex objects in the graph
    vertices::Vector{Vertex}
end

# Overload 'show' to print the whole graph in a readable way
function Base.show(io::IO, g::Graph)
    for i = 1:length(g.vertices)
        println(io, "Vertex $i, ", g.vertices[i])
    end
end

# This function tells Plots.jl how to handle an object of type 'Graph'
function Plots.plot(g::Graph; scale=1.0)
    # Get the bounding box of the coordinates to set plot limits
    xmin,xmax = extrema(v.coordinates[1] for v in g.vertices)
    ymin,ymax = extrema(v.coordinates[2] for v in g.vertices)

    sz = max(xmax-xmin, ymax-ymin)
    cr = scale*0.05sz # Circle radius
    hw = cr/2 # Not used here, but good for arrowheads

    # Set up a blank plot with no grid or axes, and equal aspect ratio
    plot(legend=false, grid=false, showaxis=false, aspect_ratio=:equal,
         xlims=[xmin-2cr, xmax+2cr], ylims=[ymin-2cr,ymax+2cr])
    
    # Points for drawing a circle
    npnts = 32
    ϕ = 2π*(0:npnts)/npnts
    cx,cy = cos.(ϕ), sin.(ϕ)    

    # Draw each vertex as a circle with its number
    for i = 1:length(g.vertices)
        c = g.vertices[i].coordinates
        plot!(c[1] .+ cr*cx, c[2] .+ cr*cy, color=:black, linewidth=2)
        annotate!(c[1], c[2], text("$i", round(Int, 14*scale), :center))
        
        # For each neighbor, draw a directed edge (arrow)
        for nb in g.vertices[i].neighbors
            cnb = g.vertices[nb].coordinates
            dc = cnb .- c
            L = sqrt(sum(dc.^2))
            # Shorten the line so it starts/ends at the circle edge
            c1 = c .+ cr/L * dc
            c2 = cnb .- cr/L * dc
            plot!([c1[1],c2[1]], [c1[2],c2[2]],
                  arrow=:simple, color=:black, linewidth=2)
        end
    end
    return plot!() # Return the final plot
end


function shortest_path_bfs(g::Graph, start, finish)
    # 'parent[i]' stores the node we came from to get to 'i'.
    # We initialize it to all zeros. 'parent[i] == 0' will mean "not visited".
    parent = zeros(Int64, length(g.vertices))
    
    S = [start] # Our queue
    # Mark 'start' as visited. We use 'start' as its own parent (a sentinel value).
    parent[start] = start
    
    while !isempty(S)
        ivertex = popfirst!(S) # Dequeue
        
        # Optimization: If we just dequeued the 'finish' node, we're done!
        # We've found the shortest path and can stop the search early.
        if ivertex == finish
            break
        end
        
        for nb in g.vertices[ivertex].neighbors
            # Use 'parent[nb] == 0' as our "not visited" check.
            if parent[nb] == 0 
                # This is the key! Record that we found 'nb' *from* 'ivertex'.
                parent[nb] = ivertex
                push!(S, nb) # Enqueue the new neighbor
            end
        end
    end
    
    # --- Path Reconstruction --- 
    path = Int64[]
    iv = finish # Start at the end
    while true
        # Add the current vertex to the front of the path
        pushfirst!(path, iv)
        # If we're back at the start, we're done
        if iv == start
            break
        end
        # "Walk backward" by moving to the parent of the current vertex
        iv = parent[iv]
    end
    return path
end

# Example graph from lecture notes
all_neighbors = [[2,10,6], [3,1,11], [1,2], [5,3,2,7], [6],
                 [7,5], [6], Int64[], [10], [1,9], [1,4,9]]
all_coordinates = [[0.81, 0.59], [0.31, 0.95], [-0.31, 0.95], [-0.81, 0.59],
                   [-1.0, 0.0],  [-0.81, -0.59], [-0.31, -0.95], [0.31, -0.95],
                   [0.81, -0.59], [1.0, -0.0], [-0.1, 0.3]]
g = Graph([Vertex(n,coordinates=c) for (n,c) in zip(all_neighbors, all_coordinates)])
plot(g)

### Problem 1: Graph to Adjacency Matrix

Write a function `convert2adjmatrix(g::Graph)` that converts our `Graph` struct into a sparse adjacency matrix. 

An adjacency matrix $A$ for a graph with $N = |V|$ vertices is an $N \times N$ matrix where $A_{ij} = 1$ if there is a directed edge *from* vertex $i$ *to* vertex $j$, and $A_{ij} = 0$ otherwise.

**Hint:** For efficiency, construct the sparse matrix by first creating vectors for the row indices ($I$), column indices ($J$), and values ($V$). Then, call `sparse(I, J, V, N, N)` just *once* at the end. This is much faster than adding elements to a sparse matrix one by one.

In [ ]:
# Test the function with our example graph
A = convert2adjmatrix(g)

# 'spy' is a useful plot function from Plots.jl
# It visualizes the sparsity pattern of a matrix (shows where the non-zeros are).
spy(A, markersize=8, title="Sparsity Pattern of Adjacency Matrix")

### Problem 2: Spanning Tree via DFS

One classic application of Depth-First Search (DFS) is finding a **spanning tree** of a graph. A spanning tree is a subgraph that includes all reachable vertices from a starting node, connected by a minimal set of edges *without forming any cycles*.

Write a function:
```julia
function spanning_tree(g::Graph, start)
```
This function should return a *new* graph, `gtree`, which has the same vertices and coordinates as `g`, but contains *only* the edges that are traversed by a standard DFS algorithm starting from the `start` vertex. 

This means an edge $(i, j)$ from `ivertex` to `nb` is added to `gtree` *if and only if* the DFS explores from $i$ and discovers $j$ as a new, unvisited node.

**Hint:** First, create a `gtree` that has all the same vertices (and their coordinates) as `g`, but with *no edges* (empty `neighbors` lists). Then, implement a recursive `visit` function for DFS. Inside this function, when you traverse an edge from `ivertex` to an *unvisited* neighbor `nb`, you should `push!` `nb` to the neighbor list of `gtree.vertices[ivertex]`.

In [ ]:
# Test the spanning_tree function, starting from node 1
gtree = spanning_tree(g, 1)

# Plot the resulting tree. Notice it has no cycles and doesn't use all edges.
plot(gtree)

### Problem 3: The Word Ladder

A *word ladder* is a puzzle where you find a sequence of words connecting a `first_word` to a `last_word`. The rules are:

1.  You can only change **one letter** at a time in each step.
2.  Every intermediate word in the sequence must be a valid word in a given dictionary.

Your task is to write a function:
```julia
function word_ladder(first_word, last_word)
```
which finds and returns the *shortest* possible word ladder (as an array of strings). 

You can assume:
* A path always exists.
* If there are multiple shortest paths, any one is a valid answer.
* `first_word` and `last_word` have the same length.

We will use the `words.txt` file from a previous homework. (Note: You'll need to download this file and place it in the same directory as your notebook for the code to work.)

**Algorithm (This is a classic graph problem!)**: 

1.  **Filter Dictionary**: Read `words.txt` and create a list (let's call it `valid_words`) containing *only* the words that have the same length as `first_word`.

2.  **Build Graph**: Create a `Graph` where each word in `valid_words` is a vertex. An *undirected edge* should exist between two vertices (words) $i$ and $j$ if and only if they differ by exactly one character.
    * *Hint:* This is the most computationally expensive part. You'll need a double loop (`for i = 1:N, j = i+1:N`).

3.  **Find Shortest Path**: The problem is now reduced to finding the shortest path in an unweighted graph. Use the `shortest_path_bfs` function from our setup code. 
    * Find the integer index (`start_index`) of `first_word` in your `valid_words` list.
    * Find the integer index (`finish_index`) of `last_word`.
    * Run `path = shortest_path_bfs(g, start_index, finish_index)`.

4.  **Return Result**: The `path` returned by BFS is a list of *indices*. Convert this back into a list of *words* from `valid_words` and return it.

**Example**:

```julia
word_ladder("fool", "sage") 
```
*Expected Output:*
```
7-element Vector{String}:
 "fool"
 "foil"
 "fail"
 "fall"
 "sall"
 "sale"
 "sage"
```

In [ ]:
# Test the function.
word_ladder("fool", "sage")